# Imports

In [220]:
from numpy import *
from numpy import pi as π
import matplotlib.pyplot as plt

import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from ipywidgets import interactive

# Utils

In [221]:
def Rx(a):
    """ Rotation matrix around the x-axis by an angle a (in radians). """
    return array([
        [1, 0, 0],
        [0, cos(a), -sin(a)],
        [0, sin(a), cos(a)]
    ])

def Ry(b):
    """ Rotation matrix around the y-axis by an angle b (in radians). """
    return array([
        [cos(b), 0, sin(b)],
        [0, 1, 0],
        [-sin(b), 0, cos(b)]
    ])

def Rz(c):
    """ Rotation matrix around the z-axis by an angle c (in radians). """
    return array([
        [cos(c), -sin(c), 0],
        [sin(c), cos(c), 0],
        [0, 0, 1]
    ])

def Rtot(a, b, c):
    """ Combine rotations around the x, y, and z axes. """
    return dot(Rz(c), dot(Ry(b), Rx(a)))

def rot2d(a, b, ang):
    """ Rotation of points on the xy plane around the z-axis """
    return (
        Rz(ang) @ vstack([a.flatten(), b.flatten(), zeros_like(a.flatten())])
    ).reshape((3, *a.shape))[:2, :, :]

In [222]:
import plotly.graph_objects as go

def plot_wavefronts(fig, surfaces):
    for surface in surfaces:
        X,Y,Z = surface
        
        fig.add_trace(go.Surface(
            x=X,
            y=Y,
            z=Z,
            opacity=0.5,
            showscale=False,
            colorscale='reds',
            showlegend=False,
            hoverinfo='none'
        ))

In [223]:
def plot_surface(fig, surface):
    X, Y, Z = surface

    fig.add_trace(go.Surface(
        x=X,
        y=Y,
        z=Z,
        opacity=0.5,
        showscale=False,
        colorscale='greys',
        showlegend=False,
        hoverinfo='none'
    ))    

# Gaussian Beam

In [224]:
class GaussianBeam:
    """
    This class is used to represent a General Astigmatic Gaussian Beam.
    """
    def __init__(self,P=1.,λ=1064e-9,q10=66e-3j,q20=-500e-3 + 266e-3j,θ=(20. + 10.j)*π/180., R=eye(3), O=zeros((3,1)), n=1.):
        self.P = P
        self.λ = λ
        self.q1 = lambda z: z + q10.real + 1.j*q10.imag
        self.q2 = lambda z: z + q20.real + 1.j*q20.imag
        self.θ = θ
        self.R = R
        self.O = O
        self.n = n

        self.k = 2.*π*self.n/λ

        self.Q = lambda z: array([
            [(cos(θ)**2.)/self.q1(z) + (sin(θ)**2.)/self.q2(z),      0.5*sin(2.*θ)*(1./self.q1(z) - 1./self.q2(z))],
            [0.5*sin(2.*θ)*(1./self.q1(z) - 1./self.q2(z)),      (sin(θ)**2.)/self.q1(z) + (cos(θ)**2.)/self.q2(z)]
        ],complex128)
        self.E0 = lambda z: sqrt(P/λ*sqrt(
            4.*self.Q(z)[0,0].imag)*self.Q(z)[1,1].imag - (self.Q(z)[0,1] + self.Q(z)[1,0])**2.
        )
        self.η = lambda z: 0.5*(atan(self.q1(z).real/self.q1(z).imag) + atan(self.q2(z).real/self.q2(z).imag))
        self.E = lambda r,z: self.E0(z)*exp(1.j*self.η(z) - 1.j*(self.k/2.)*(r.T @ self.Q(z) @ r))
    
    @staticmethod
    def simple_astigmatic(P=1., λ=700e-9, θ1=6.*π/180., θ2=12.*π/180., θ=0., R=eye(3), O=zeros((3,1)),n=1.):
        """
        This function is used to redefine the beam as simple astigmatic using the divergence in the x and y directions.
        """
        w10 = λ / (π * θ1)
        w20 = λ / (π * θ2)

        z10 = (π * (w10 ** 2.)) / λ
        z20 = (π * (w20 ** 2.)) / λ

        q10 = 1.j * z10
        q20 = 1.j * z20

        return GaussianBeam(P, λ, q10, q20, θ, R, O, n)

    @staticmethod
    def get_q_parameters_from_Q(Q):
        """
        This static method is used to get the q-parameters and the complex angle θ of a beam given its complex radius
          of curvature tensor Q.
        """
        q1, q2 = 1./linalg.eigvals(Q)
        θ = 0.5*atan((Q[0,1] + Q[1,0]) / (Q[0,0] - Q[1,1]))

        return q1, q2, θ

    def get_elipses_parameters(self,z):
        """
        This function is used to calculate the real parameters needed for intensity and phase ellipses to be drawn
        """

        α = self.θ.real
        β = self.θ.imag
        
        ρ1 = self.q1(z).real/(abs(self.q1(z))**2.)
        ρ2 = self.q2(z).real/(abs(self.q2(z))**2.)

        ω1 = self.q1(z).imag/(abs(self.q1(z))**2.)
        ω2 = self.q2(z).imag/(abs(self.q2(z))**2.)

        return α, β, ρ1, ρ2, ω1, ω2
    
    def intensity_ellipse(self, z):
        """
        This function returns the semi axis and rotation of the intensity elipse.
            
        The intensity elipse (defined by φ_w, w1 and w2 - the angle of rotation and semi-axis) is drawn on the
        plane paralel to xy and containing the informed z point on the axis z, and define the waist shape on the
        corresponding z point.
        """

        α, β, ρ1, ρ2, ω1, ω2 = self.get_elipses_parameters(z)

        φ_w0 = 0.5*arctan2(-(ρ1 - ρ2)*tanh(2.*β),(ω1 - ω2))
        φ_w = unwrap(φ_w0 + α, period=π)

        w1 = 1./sqrt((self.k/4.)*(ω1 + ω2 + sqrt(((ω1 - ω2)**2.)*(cosh(2*β)**2.) + ((ρ1 - ρ2)**2.)*(sinh(2*β)**2.))))
        w2 = 1./sqrt((self.k/4.)*(ω1 + ω2 - sqrt(((ω1 - ω2)**2.)*(cosh(2*β)**2.) + ((ρ1 - ρ2)**2.)*(sinh(2*β)**2.))))

        return φ_w, w1, w2
        
    def phase_ellipse(self, z):
        """
        This function returns the semi axis and rotation of the phase elipse.

        The phase elipse is the elipsoid of curvature matrix:
        C = [[1/R1, 0],[0, 1/R2]]
        on its own coordinate system located at the informed z, with local z equal to global z but axis x and y
        rotated by φ_R around z. This elipsoide is tangent to the point z with concavity directed to the origin of
        the global axis.
        """

        α, β, ρ1, ρ2, ω1, ω2 = self.get_elipses_parameters(z)

        φ_R0 = 0.5*arctan2( (ω1 - ω2)*tanh(2.*β),(ρ1 - ρ2))
        φ_R = unwrap(φ_R0 + α, period=π)

        R1 = 2./(ρ1 + ρ2 + sqrt(((ρ1 - ρ2)**2.)*(cosh(2*β)**2.) + ((ω1 - ω2)**2.)*(sinh(2*β)**2.)))
        R2 = 2./(ρ1 + ρ2 - sqrt(((ρ1 - ρ2)**2.)*(cosh(2*β)**2.) + ((ω1 - ω2)**2.)*(sinh(2*β)**2.)))

        return φ_R, R1, R2
    
    def wavefront_surfaces(self, z, n_points=50, coordinates=None):
        """
        This function uses the intensity and phase elipses to calculate wavefronts within the beam waist as
        surfaces with the curvature given by the phase ellipse data and waist given by the intensity elipse data.
        """
        φ_w, w1, w2 = self.intensity_ellipse(z)
        φ_R, R1, R2 = self.phase_ellipse(z)

        θ = linspace(0., 2*π, n_points)
        ρ = linspace(0., 1., n_points)

        Θ, P = meshgrid(θ, ρ)

        surfaces = []
        for zi, w1i, w2i, φ_wi, R1i, R2i, φ_Ri in zip(z, w1, w2, φ_w, R1, R2, φ_R):
            Xw = w1i * P * cos(Θ)
            Yw = w2i * P * sin(Θ)

            X, Y = rot2d(Xw, Yw, φ_wi)

            XR, YR = rot2d(X, Y, -φ_Ri)
            Z = zi - (0.5 * (XR ** 2.) / R1i + 0.5 * (YR ** 2.) / R2i)

            if isinstance(coordinates, list):
                R = coordinates[0]
                O = coordinates[1]
            elif isinstance(coordinates, str) and (coordinates == "local"):
                R = eye(3)
                O = zeros((3,1))
            else:
                R = self.R
                O = self.O

            X, Y, Z = ((R @ vstack([X.flatten(), Y.flatten(), Z.flatten()])) + O).reshape((3, *X.shape))

            surfaces.append([X,Y,Z])

        return surfaces


In [225]:
gb_ga = GaussianBeam()

z_ga = linspace(-1,1,30)
surfaces_ga = gb_ga.wavefront_surfaces(z_ga)

fig_ga = go.Figure()

plot_wavefronts(fig_ga, surfaces_ga)

fig_ga.update_layout(
    title="Visualização 3D da Cintura e Elipsoide de Curvatura",
    scene=dict(
        xaxis=dict(title='X (m)'),
        yaxis=dict(title='Y (m)'),
        zaxis=dict(title='Z (m)'),
    ),
    autosize=False,
    width=800,
    height=600
)

fig_ga.show()

In [226]:
gb_sa = GaussianBeam.simple_astigmatic(R=Rx(-π/4))

z_sa = linspace(-1e-3, 1e-3, 30)
surfaces_sa = gb_sa.wavefront_surfaces(z_sa)

fig_sa = go.Figure()

plot_wavefronts(fig_sa, surfaces_sa)

fig_sa.update_layout(
    title="Visualização 3D da Cintura e Elipsoide de Curvatura",
    scene=dict(
        xaxis=dict(title='X (m)'),
        yaxis=dict(title='Y (m)'),
        zaxis=dict(title='Z (m)'),
    ),
    autosize=False,
    width=800,
    height=600
)

fig_sa.show()

In [227]:
q1, q2, θ = GaussianBeam.get_q_parameters_from_Q(gb_ga.Q(0))

print(q1)
print(q2)
print(180/π*θ)

(-0+0.066j)
(-0.5000000000000006+0.266j)
(20+10j)


# Surface

In [ ]:
class Surface:
    """
    This class models
    """
    def __init__(self, R=eye(3), O=zeros((3,1)), A=inf, B=inf, C=1., n=1.45):
        self.R = R
        self.O = O
        self.S = diag([1. / (A ** 2.), 1. / (B ** 2.), 1. / (C ** 2.)])
        self.n = n

    def surface(self, n_points=50, xrange=[-1., 1.], yrange=[-1.,1.], zrange=[-1., 1.]):
        """
        This function returns points in global coordinates for plotting the surface.
        """
        cx, cy, cz = sqrt(diag(self.S))
        
        if (cx == 0.) and (cy == 0):
            x = linspace(xrange[0], xrange[1], n_points)
            y = linspace(yrange[0], yrange[1], n_points)
            [X, Y] = meshgrid(x, y)

            Z = - 1./cz * ones(X.shape)
        
        elif (cx == 0):
            θ = linspace(-π/2, π/2, n_points)
            x = linspace(-1., 1., n_points)
            y = (1./cy) * cos(θ)

            [X, Y] = meshgrid(x, y)

            Z = -(1./cz) + (cy * (Y ** 2.))
        
        else:
            A, B, C = [1./c for c in [cx, cy, cz]]

            θ = linspace(-π/2, π/2, n_points)
            φ = linspace(-π/2, π/2, n_points)
            [Θ, Φ] = meshgrid(θ, φ)

            X = A * cos(Θ) * sin(Φ)
            Y = B * sin(Θ) * cos(Φ)
            Z = C * cos(Φ)
        
        X, Y, Z = (self.R @ (vstack([X.flatten(), Y.flatten(), Z.flatten()])) + self.O).reshape((3,*X.shape))

        return [X,Y,Z]


    def point_of_incidence(self, gb: GaussianBeam):
        """
        This function calculates the point of incidence of the beam on the surface expressed in (in order) the surface,
        beam and global coordinates.
        """
        k = gb.R @ array([[0],[0],[1]])
        k_prime = self.R.T @ k
        O_prime = self.R.T @ (gb.O - self.O)

        a = k_prime.T @ self.S @ k_prime
        b = 2. * (k_prime.T @ self.S @ O_prime)
        c = O_prime.T @ self.S @ O_prime - 1.

        r = roots(vstack([a,b,c]).flatten())
        t = min(r[r >= 0])

        return [(k_prime * t) + O_prime, gb.R.T @ (k * t - gb.O), (k * t) + gb.O]
        
    def get_local_coordinates(self, Ps):
        """
        This function calculates de othonormal basis of the point of incidence coordinate system expressed 
        in the surface coordinate system. The point of incidence must be expressed in the surface coordinates.
        """

        n = (2 * (self.S @ Ps)).flatten()
        n = n / linalg.norm(n)

        d1 = cross(array([0,1,0]), n)
        d1 = d1 / linalg.norm(d1)

        d2 = cross(n, d1)

        return [d.reshape(3,1) for d in [d1,d2,n]]

    def get_curvature_matrix(self, Ps):
        """
        This function calculates de curature matrix of the surface in a given point of incidence. This curvature matrix is
        expressed in the local coordinates system (coordinate system of the point of incidence). The point of incidence must
        be expressed in surface coordinates.
        """
        M = hstack(self.get_local_coordinates(Ps))

        S = M @ self.S @ M.T

        tx = Ps.flatten()[0]
        ty = Ps.flatten()[1]


        b = (((S[0,2]*tx + S[1,2]*ty)**2.) - S[2,2]*(S[0,0]*(tx**2.) + 2.*S[0,1]*tx*ty + S[1,1]*(ty ** 2.) - 1)) ** (3./2.)
        g = S[0,0]*(S[1,2]**2.) + S[1,1]*(S[0,2]**2.) + S[2,2]*(S[0,1]**2.) - 2.*S[0,1]*S[0,2]*S[1,2] - S[0,0]*S[1,1]*S[2,2]

        return (1/b) * array(
            [[S[0,0]*S[2,2] - (S[0,2]**2.) + g*(ty**2.), S[0,1]*S[2,2] - S[0,2]*S[1,2] - g*tx*ty],
             [S[0,1]*S[2,2] - S[0,2]*S[1,2] - g*tx*ty, S[1,1]*S[2,2] - (S[1,2]**2.) + g*(tx**2.)]]
        )

    def reflect_and_refract(self, gb: GaussianBeam):
        """
        This function calculates the parameters needed to describe the transmitted and reflected beam.
        These parameters are the orthonormal basis of the transmitted and reflected beams and their complex radius of curvature tensor.
        """
        Ps, Pb, Pg = self.point_of_incidence(gb)
        d1, d2, n = self.get_local_coordinates(Ps)
        C = self.get_curvature_matrix(Ps)

        # We need to express beam coordinates in surface coordinates
        xi, yi, zi = [(self.R.T @ gb.R)[:,i].reshape((3, 1)) for i in range(3)]
        Qi = gb.Q(Pb[2,0])

        ni = gb.n
        nt = self.n

        # Law or reflection
        zr = zi - 2 * (zi.T @ n) * n
        
        xr = cross(array([0,1,0]), zr.flatten()).reshape((3,1))
        xr = xr / linalg.norm(xr)
        yr = cross(zr.flatten(), xr.flatten()).reshape((3,1))
        
        # Law of refraction
        αi = acos(- (n.T @ zi))
        αt = asin((ni / nt) * sin(αi))
        zt = (ni / nt) * zi + (cos(αt) - (ni / nt) * cos(αi))*n

        xt = cross(array([0,1,0]), zt.flatten()).reshape((3,1))
        xt = xt / linalg.norm(xt)
        yt = cross(zt.flatten(), xt.flatten()).reshape((3,1))
        
        K = lambda xl, yl: array([[xl.T @ d1, xl.T @ d2],[yl.T @ d1, yl.T @ d2]]).reshape((2,2))

        Ki = K(xi, yi)
        Kr = K(xr, yr)
        Kt = K(xt, yt)

        Qr = linalg.inv(Kr.T) @ (Ki.T @ Qi @ Ki - C * ((n.T @ zi) - (n.T @ zr))) @ linalg.inv(Kr)
        Qt = (ni / nt) * (linalg.inv(Kt.T) @ (Ki.T @ Qi @ Ki - C * ((n.T @ zi) - (nt / ni) * (n.T @ zt))) @ linalg.inv(Kt))

        q1i, q2i, θi = GaussianBeam.get_q_parameters_from_Q(Qi)
        q1r, q2r, θr = GaussianBeam.get_q_parameters_from_Q(Qr)
        q1t, q2t, θt = GaussianBeam.get_q_parameters_from_Q(Qt)

        Ri = self.R @ hstack([xi,yi,zi])
        Rr = self.R @ hstack([xr,yr,zr])
        Rt = self.R @ hstack([xt,yt,zt])
        
        gbi = GaussianBeam(gb.P, gb.λ, q1i, q2i, θi, Ri, Pg, ni)
        gbr = GaussianBeam(gb.P, gb.λ, q1r, q2r, θr, Rr, Pg, ni)
        gbt = GaussianBeam(gb.P, gb.λ, q1t, q2t, θt, Rt, Pg, nt)
        
        return gbi, gbr, gbt


In [229]:
gb = GaussianBeam.simple_astigmatic(R=Rx(-pi/3))
plane = Surface(O=array([[0,0,1 + 1e-12]]).T)

gbi, gbr, gbt = plane.reflect_and_refract(gb)

zi = linspace(-10e-3,0.,30)
zr = linspace(0.,10e-3,30)
zt = linspace(0.,10e-3,20)

surfaces_i = gbi.wavefront_surfaces(zi)
surfaces_r = gbr.wavefront_surfaces(zr)
surfaces_t = gbt.wavefront_surfaces(zt)

fig = go.Figure()

plot_wavefronts(fig, [*surfaces_i, *surfaces_r])

surface = plane.surface()
plot_surface(fig, surface)

fig.update_layout(
    title="Visualização 3D da Cintura e Elipsoide de Curvatura",
    scene=dict(
        xaxis=dict(title='X (m)',range=[-0.01, 0.01]),
        yaxis=dict(title='Y (m)',range=[-0.01, 0.01]),
        zaxis=dict(title='Z (m)',range=[-0.01, 0.01]),
    ),
    autosize=False,
    width=800,
    height=600,
)